In [ ]:
# Executor profile
#
# Instrumented executor functions:
#   * spin
#       * get_next_executable
#           * get_next_ready_executable
#           * wait_for_work
#       * execute_any_executable
#
# Get trace data
# (unfortunately we cannot use tracetools_launch since the
#  lttng Python bindings don't support enabling the 'ip'
#  context, which is needed if we want to have the
#  name of the function with a func_entry event):
#   $ cd ros2_ws/
#   $ lttng create executor-profile
#   $ lttng enable-channel -u ros --subbuf-size=8M
#   $ lttng enable-channel -k kernel --subbuf-size=8M
#   $ lttng enable-event -c ros -u lttng_ust_cyg_profile_fast:func_entry
#   $ lttng enable-event -c ros -u lttng_ust_cyg_profile_fast:func_exit
#   $ lttng enable-event -c ros -u lttng_ust_statedump:start
#   $ lttng enable-event -c ros -u lttng_ust_statedump:end
#   $ lttng enable-event -c ros -u lttng_ust_statedump:bin_info
#   $ lttng enable-event -c ros -u lttng_ust_statedump:build_id
#   $ lttng enable-event -c kernel -k sched_switch
#   $ lttng add-context -u -t vtid -t vpid -t procname -t ip
#   $ lttng start
#   $ LD_PRELOAD=/usr/lib/x86_64-linux-gnu/liblttng-ust-cyg-profile-fast.so ./build/ros_performance/ros
#   (wait a few seconds, then kill with Ctrl+C)
#   $ lttng stop
#   $ lttng destroy
#
# Then set the path to the trace directory below (trace directory should be under ~/lttng-traces/)

In [1]:
trace_directory = '~/lttng-traces/profile-ros-instr-overall-20190813-135724'

In [2]:
import sys
# Assuming a workspace with:
#   src/tracetools_analysis/
#   src/micro-ROS/ros_tracing/ros2_tracing/tracetools_read/
sys.path.insert(0, '../')
sys.path.insert(0, '../../../micro-ROS/ros_tracing/ros2_tracing/tracetools_read/')
import datetime as dt
import os

from bokeh.palettes import Category20
from bokeh.plotting import figure
from bokeh.plotting import output_notebook
from bokeh.io import show
from bokeh.layouts import row, column
from bokeh.models import ColumnDataSource
from bokeh.models import DatetimeTickFormatter
from bokeh.models import PrintfTickFormatter
from bokeh.models.widgets import Div
import numpy as np
import pandas as pd

from tracetools_analysis import utils
from tracetools_analysis.conversion import ctf
from tracetools_analysis.loading import load_pickle
from tracetools_analysis.processor import Processor
from tracetools_analysis.processor.cpu_time import CpuTimeHandler
from tracetools_analysis.processor.profile import ProfileHandler

In [3]:
# Convert
trace_directory = os.path.expanduser(trace_directory)
pickle_filename = 'pickle'
pickle_path = os.path.join(trace_directory, pickle_filename)
count = ctf.convert(trace_directory, pickle_path)
print(f'{count} events')

299302 events


In [4]:
# Process
events = load_pickle(pickle_path)
# get addresses with
#   $ babeltrace executor-profile* | grep func_entry
address_to_func = {
    '0x7F4B527974D6': 'spin',
    '0x7F4B527929A6': 'get_next_executable',
    '0x7F4B5279288E': 'get_next_ready_executable',
    '0x7F4B5278F048': 'wait_for_work',
    '0x7F4B52790F16': 'execute_any_executable',
}
profile_handler = ProfileHandler(address_to_func=address_to_func)
cpu_handler = CpuTimeHandler()
processor = Processor(profile_handler, cpu_handler)

In [5]:
processor.process(events)

In [6]:
profile_util = utils.ProfileDataModelUtil(profile_handler.data)
cpu_util = utils.CpuTimeDataModelUtil(cpu_handler.data)

output_notebook()
psize = 450

tids = profile_util.get_tids()
print(tids)

Loading BokehJS ...

{16885}


In [7]:
# Select the first one, since we only have one in this case anyway
tid = list(tids)[0]

In [8]:
# Convert time columns
_ = utils.DataModelUtil.convert_time_columns(
    profile_handler.data.times,
    ['duration', 'actual_duration'],
    ['start_timestamp'],
)

In [10]:
# Plot invididual function durations
functions_data = profile_util.get_function_duration_data(tid)
for function_data in functions_data:
    depth = function_data['depth']
    name = function_data['function_name']
    parent = function_data['parent_name']
    df = function_data['data']

    # Duration vs. actual duration
    starttime = df['start_timestamp'].iloc[0].strftime('%Y-%m-%d %H:%M')
    duration_source = ColumnDataSource(df)
    duration = figure(
        title=f'Function duration over time',
        x_axis_label=f'start ({starttime})',
        y_axis_label='duration (ms)',
        plot_width=psize, plot_height=psize,
    )
    duration.title.align = 'center'
    duration.varea_stack(
        ['actual_duration', 'duration_difference'],
        x='start_timestamp',
        color=('blue', 'red'),
        legend=('ON CPU', 'OFF CPU'),
        source=duration_source,
    )
    duration.legend.label_text_font_size = '11px'
    duration.xaxis[0].formatter = DatetimeTickFormatter(seconds=['%Ss'])

    # Histogram
    dur_hist_overall, edges_overall = np.histogram(df['duration'], bins=10)
    dur_hist_actual, edges_actual = np.histogram(df['actual_duration'], bins=10)
    duration_hist_overall = pd.DataFrame({
        'duration': dur_hist_overall, 
        'left': edges_overall[:-1], 
        'right': edges_overall[1:],
    })
    duration_hist_actual = pd.DataFrame({
        'actual_duration': dur_hist_actual, 
        'left': edges_actual[:-1], 
        'right': edges_actual[1:],
    })
    histogram = figure(
        title=f'Distribution',
        x_axis_label='duration (ms)',
        y_axis_label='frequency',
        plot_width=psize, plot_height=psize,
    )
    histogram.title.align = 'center'
    histogram.quad(
        bottom=0, top=duration_hist_overall['duration'],
        left=duration_hist_overall['left'], right=duration_hist_overall['right'],
        legend='overall duration',
        color='blue',
    )
    histogram.quad(
        bottom=0, top=duration_hist_actual['actual_duration'],
        left=duration_hist_actual['left'], right=duration_hist_actual['right'],
        legend='ON CPU',
        color='red',
    )

    show(column(Div(text=f'<h2>{name}()</h2>'),
                row(duration, histogram)))

# Comparison
colors = Category20[20]

data = {
    'depth': ['2'],
}
elements = []
legend = []
for function_data in functions_data:
    depth = function_data['depth']
    if depth != 2:
        continue
    name = function_data['function_name']
    actual_duration_mean = function_data['data']['actual_duration'].mean()
    duration_mean_diff = function_data['data']['duration_difference'].mean()
    actual_string = f'{name}, actual'
    diff_string = f'{name}, duration-actual'
    data[actual_string] = [actual_duration_mean]
    data[diff_string] = [duration_mean_diff]
    elements.append(actual_string)
    elements.append(diff_string)
    legend.append(f'{name}() ON CPU: {actual_duration_mean:.4f}')
    legend.append(f'{name}() OFF CPU: {duration_mean_diff:.4f}')

comparison = figure(
    y_range=['2'],
    title=f'Mean durations comparison',
    x_axis_label='mean duration (ms)',
    y_axis_label='depth',
    tooltips='$name: @$name{1.11}',
    plot_width=psize+200, plot_height=psize,
)
comparison.hbar_stack(
    elements, y='depth', height=0.3,
    color=colors[:(len(elements))],
    source=data,
    legend=legend,
)
comparison.title.align = 'center'
comparison.legend.label_text_font_size = '10px'
show(comparison)


In [27]:
# CPU time

# { function_name|'thread' --> {
#      'parent_name': parent function name,
#      'overall': overall duration,
#      'actual': actual duration,
#      'cpu': cpu usage of the function by itself (%),
#      'thread': actual duration wrt thread (%),
#      'parent': actual duration wrt parent function (%),
#   }
# }
cputime = {}


# * for the whole process/thread
time_per_thread = cpu_util.get_time_per_thread()
times_tid = cpu_handler.data.times[cpu_handler.data.times['tid'] == tid]
begin = times_tid.iloc[0]['start_timestamp']
end = times_tid.iloc[-1]['start_timestamp'] + times_tid.iloc[-1]['duration']
overall = (end - begin) / (1000000.0 * 1000.0)
actual = time_per_thread.loc[tid, 'duration'] / (1000000.0 * 1000.0)
cpu_percent = 100.0 * (actual / overall)
cputime['thread'] = dict(
    parent_name='-',
    overall=overall,
    actual=actual,
    cpu=cpu_percent,
    thread=100.0,
)

# * for individual functions 
for function_data in functions_data:
    name = function_data['function_name']
    data = function_data['data']

    overall = (data['duration'].sum() / 1000.0)
    actual = (data['actual_duration'].sum() / 1000.0)
    cpu_percent = 100.0 * (actual / overall)
    percentage_thread = 100.0 * (actual / cputime['thread']['actual'])
    cputime[name] = dict(
        parent_name=function_data['parent_name'],
        overall=overall,
        actual=actual,
        cpu=cpu_percent,
        thread=percentage_thread,
    )

# * for individual functions wrt their parent
for function_name in cputime.keys():
    if function_name in ['thread', 'spin']:
        continue
    parent_name = cputime[function_name]['parent_name']
    parent_actual = cputime[parent_name]['actual']
    cputime[function_name]['parent'] = 100.0 * (cputime[function_name]['actual'] / parent_actual)

for name in cputime.keys():
    print()
    print(f'Function: {name} (parent: {cputime[name]["parent_name"]})')
    print(f'\toverall duration              : {cputime[name]["overall"]:02.02f} s')
    print(f'\tactual duration               : {cputime[name]["actual"]:02.02f} s')
    print(f'\tCPU usage, function by itself : {cputime[name]["cpu"]:02.02f} %')
    print(f'\tactual duration, wrt thread   : {cputime[name]["thread"]:02.02f} %')
    if name not in ['thread', 'spin']:
        print(f'\tactual duration, wrt parent   : {cputime[name]["parent"]:02.02f} %')



Function: thread (parent: -)
	overall duration              : 2.93 s
	actual duration               : 1.64 s
	CPU usage, function by itself : 55.87 %
	actual duration, wrt thread   : 100.00 %

Function: get_next_ready_executable (parent: get_next_executable)
	overall duration              : 0.87 s
	actual duration               : 0.87 s
	CPU usage, function by itself : 99.46 %
	actual duration, wrt thread   : 53.09 %
	actual duration, wrt parent   : 67.02 %

Function: get_next_executable (parent: spin)
	overall duration              : 2.44 s
	actual duration               : 1.30 s
	CPU usage, function by itself : 53.16 %
	actual duration, wrt thread   : 79.21 %
	actual duration, wrt parent   : 88.04 %

Function: execute_any_executable (parent: spin)
	overall duration              : 0.14 s
	actual duration               : 0.13 s
	CPU usage, function by itself : 97.00 %
	actual duration, wrt thread   : 8.22 %
	actual duration, wrt parent   : 9.13 %

Function: wait_for_work (parent: get_

In [154]:
colors = Category20[20]

def plot_comparison(target_functions):
    data_comparison = {
        'compared to': ['thread', 'parent function'],
    }
    elements_comparison = []
    legend_comparison = []
    for name in target_functions:
        actual_percentage_thread = cputime[name]['thread']
        actual_percentage_parent = cputime[name]['parent']
        string_thread = f'{name}, wrt thread'
        string_function = f'{name}, wrt parent function'
        data_comparison[string_thread] = [actual_percentage_thread, 0.0]
        data_comparison[string_function] = [0.0, actual_percentage_parent]
        elements_comparison.append(string_thread)
        elements_comparison.append(string_function)
        legend_comparison.append(f'{name}() wrt thread ON CPU: {actual_percentage_thread:.2f} %')
        legend_comparison.append(f'{name}() wrt parent ON CPU: {actual_percentage_parent:.2f} %')

    comparison_fig = figure(
        y_range=['parent function', 'thread'],
        title='ON CPU time comparison (wrt whole thread & parent function)',
        x_axis_label='proportion (%)',
        y_axis_label='compared to',
        tooltips='$name: @$name{1.11} %',
        plot_width=psize+400, plot_height=psize,
    )
    comparison_fig.hbar_stack(
        elements_comparison,
        y='compared to',
        height=0.3,
        color=colors[:(len(elements_comparison))],
        source=data_comparison,
        legend=legend_comparison,
    )
    comparison_fig.title.align = 'center'
    comparison_fig.title.text_font_size = '20px'
    comparison_fig.legend.label_text_font_size = '10px'
    show(comparison_fig)

def plot_cpu_usage(target_functions):
    data_cpuusage = {
        'function': [],
        'usage': []
    }
    for name in target_functions:
        cpu_usage = cputime[name]['cpu']
        data_cpuusage['function'].append(name)
        string_cpuusage = f'{name}, CPU usage'
        data_cpuusage['usage'].append(cpu_usage)

    cpu_usage_fig = figure(
        x_range=data_cpuusage['function'],
        title='CPU usage for individual functions (actual / overall time)',
        x_axis_label='function',
        y_axis_label='CPU usage (%)',
        plot_width=psize+100, plot_height=psize+200,
    )
    cpu_usage_fig.vbar(
        x=data_cpuusage['function'],
        top=data_cpuusage['usage'],
        width=0.5,
        color=colors[::2][:(len(data_cpuusage['function']))],
    )
    cpu_usage_fig.xaxis.major_label_orientation = 3.1415/3
    cpu_usage_fig.title.align = 'center'
    cpu_usage_fig.title.text_font_size = '13px'
    show(cpu_usage_fig)
    

In [151]:
plot_comparison(['get_next_executable', 'execute_any_executable'])

In [152]:
plot_comparison(['get_next_ready_executable', 'wait_for_work'])

In [155]:
plot_cpu_usage([
    'thread',
    'spin',
    'get_next_executable',
    'get_next_ready_executable',
    'wait_for_work',
    'execute_any_executable',
])